## SDK code to create CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_28d

Feature description:
>Similarity between the customer and all customers measured by the Cosine Similarity between the Distribution representing the cumulative TotalCost of item, categorized by their respective product's ProductGroup, over 28d for both entities.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Set windows for aggregation

In [ ]:
windows = ['28d']

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")

In [ ]:
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

### Join views
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(groceryproduct_view, rsuffix="")

### Do window aggregation from INVOICEITEMS
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation over time](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)

 See [SDK reference for feature group](https://docs.featurebyte.com/latest/reference/core/feature_group/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

In [ ]:
# Group INVOICEITEMS view by customer entity (GroceryCustomerGuid) across different ProductGroups.
invoiceitems_view_by_customer_across_productgroup =\
invoiceitems_view.groupby(
    ['GroceryCustomerGuid'], category="ProductGroup"
)

In [ ]:
# Distribution representing the cumulative TotalCost of item, categorized by their respective
# product's ProductGroup, for the customer over time.
feature_group =\
invoiceitems_view_by_customer_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "CUSTOMER_item_TotalCost_across_product_ProductGroups"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get CUSTOMER_item_TotalCost_across_product_ProductGroups_28d object from feature group.
customer_item_totalcost_across_product_productgroups_28d =\
feature_group["CUSTOMER_item_TotalCost_across_product_ProductGroups_28d"]

In [ ]:
# Group INVOICEITEMS view across different ProductGroups.
invoiceitems_view_by_overall_across_productgroup =\
invoiceitems_view.groupby(
    [], category="ProductGroup"
)

In [ ]:
# Distribution representing the cumulative TotalCost of item, categorized by their respective
# product's ProductGroup, over time.
feature_group =\
invoiceitems_view_by_overall_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "OVERALL_item_TotalCost_across_product_ProductGroups"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get OVERALL_item_TotalCost_across_product_ProductGroups_28d object from feature group.
overall_item_totalcost_across_product_productgroups_28d =\
feature_group["OVERALL_item_TotalCost_across_product_ProductGroups_28d"]

### Derive Similarity feature across entities
 See [list of feature transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

In [ ]:
# Derive Similarity feature from cosine similarity between
# CUSTOMER_item_TotalCost_across_product_ProductGroups_28d
# and OVERALL_item_TotalCost_across_product_ProductGroups_28d
customer_vs_overall_item_totalcost_across_product_productgroups_28d =\
customer_item_totalcost_across_product_productgroups_28d.cd.cosine_similarity(
        overall_item_totalcost_across_product_productgroups_28d
    )
# Give a name to new feature
customer_vs_overall_item_totalcost_across_product_productgroups_28d.name = \
"CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_28d"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
customer_vs_overall_item_totalcost_across_product_productgroups_28d.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 Customers"
).to_pandas()

In [ ]:
#Preview CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_28d
customer_vs_overall_item_totalcost_across_product_productgroups_28d.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
customer_vs_overall_item_totalcost_across_product_productgroups_28d.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
customer_vs_overall_item_totalcost_across_product_productgroups_28d.update_description(
	"Similarity between the customer and all customers measured by the "
	"Cosine Similarity between the Distribution representing the cumulative"
	" TotalCost of item, categorized by their respective product's "
	"ProductGroup, over 28d for both entities."
)
# See feature definition file
customer_vs_overall_item_totalcost_across_product_productgroups_28d.definition